# SCE-TTS: 음성합성 데모

이 문서는 SCE-TTS 프로젝트의 음성 합성 데모입니다.

이 데모에 대한 더 자세한 정보는 아래 링크에서 확인하실 수 있습니다.  
https://sce-tts.github.io/

## 1. 구글 드라이브 마운트

음성합성을 위해 학습한 모델이 있는 구글 드라이브를 마운트합니다.  
마운트할 구글 드라이브 내에 다음 파일들이 존재하는지 꼭 확인해주세요.

- `/Colab Notebooks/data/glowtts-v2/model_file.pth.tar`
- `/Colab Notebooks/data/glowtts-v2/config.json`
- `/Colab Notebooks/data/hifigan-v2/model_file.pth.tar`
- `/Colab Notebooks/data/hifigan-v2/config.json`


(존재하지 않는다면, [glowtts-v2.zip](https://drive.google.com/file/d/1DMKLdfZ_gzc_z0qDod6_G8fEXj0zCHvC/view?usp=sharing), [hifigan-v2.zip](https://drive.google.com/file/d/1vRxp1RH-U7gSzWgyxnKY4h_7pB3tjPmU/view?usp=sharing)을 내려받아 준비해주세요.)

만약 아래에 `Enter your authorization code:`과 같은 메시지가 출력될 경우,  
같이 출력된 링크에 접속하여, 마운트할 구글 계정을 선택하신 후, 인증 코드를 복사하여 입력해주세요.

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


## 2. 필수 라이브러리 및 함수 불러오기

실행에 필요한 라이브러리 및 함수를 불러옵니다.

이 과정은 약 10분 정도 소요될 수 있습니다.

In [2]:
import os
import sys
from pathlib import Path

In [3]:
%cd /content
!git clone --depth 1 https://github.com/sce-tts/TTS.git -b sce-tts
!git clone --depth 1 https://github.com/sce-tts/g2pK.git
%cd /content/TTS
!pip install -q --no-cache-dir -e .
%cd /content/g2pK
!pip install -q --no-cache-dir "konlpy" "jamo" "nltk" "python-mecab-ko"
!pip install -q --no-cache-dir -e .

/content
Cloning into 'TTS'...
remote: Enumerating objects: 447, done.
remote: Counting objects: 100% (447/447), done.
remote: Compressing objects: 100% (413/413), done.
remote: Total 447 (delta 56), reused 211 (delta 22), pack-reused 0
Receiving objects: 100% (447/447), 13.77 MiB | 23.85 MiB/s, done.
Resolving deltas: 100% (56/56), done.
Cloning into 'g2pK'...
remote: Enumerating objects: 20, done.
remote: Counting objects: 100% (20/20), done.
remote: Compressing objects: 100% (20/20), done.
remote: Total 20 (delta 0), reused 14 (delta 0), pack-reused 0
Receiving objects: 100% (20/20), 35.24 KiB | 1.96 MiB/s, done.
/content/TTS
  error: subprocess-exited-with-error
  
  × pip subprocess to install build dependencies did not run successfully.
  │ exit code: 1
  ╰─> See above for output.
  
  note: This error originates from a subprocess, and is likely not a problem with pip.
  Installing build dependencies ... error
error: subprocess-exited-with-error

× pip subprocess to install build

In [4]:
%cd /content/g2pK
import g2pk
g2p = g2pk.G2p()

/content/g2pK


[nltk_data] Downloading package cmudict to /root/nltk_data...
[nltk_data]   Unzipping corpora/cmudict.zip.


In [5]:
!pip install pysbd coqpit unidecode pypinyin librosa==0.9.1

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 71.1/71.1 kB 1.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 235.5/235.5 kB 6.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.4/1.4 MB 9.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 213.1/213.1 kB 9.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 17.7 MB/s eta 0:00:00
  Attempting uninstall: librosa
    Found existing installation: librosa 0.10.1
    Uninstalling librosa-0.10.1:
      Successfully uninstalled librosa-0.10.1


In [6]:
%cd /content/TTS
import re
import sys
from unicodedata import normalize
import IPython

from TTS.utils.synthesizer import Synthesizer

def normalize_text(text):
    text = text.strip()

    for c in ",;:":
        text = text.replace(c, ".")
    text = remove_duplicated_punctuations(text)

    text = jamo_text(text)

    text = g2p.idioms(text)
    text = g2pk.english.convert_eng(text, g2p.cmu)
    text = g2pk.utils.annotate(text, g2p.mecab)
    text = g2pk.numerals.convert_num(text)
    text = re.sub("/[PJEB]", "", text)

    text = alphabet_text(text)

    # remove unreadable characters
    text = normalize("NFD", text)
    text = "".join(c for c in text if c in symbols)
    text = normalize("NFC", text)

    text = text.strip()
    if len(text) == 0:
        return ""

    # only single punctuation
    if text in '.!?':
        return punctuation_text(text)

    # append punctuation if there is no punctuation at the end of the text
    if text[-1] not in '.!?':
        text += '.'

    return text


def remove_duplicated_punctuations(text):
    text = re.sub(r"[.?!]+\?", "?", text)
    text = re.sub(r"[.?!]+!", "!", text)
    text = re.sub(r"[.?!]+\.", ".", text)
    return text


def split_text(text):
    text = remove_duplicated_punctuations(text)

    texts = []
    for subtext in re.findall(r'[^.!?\n]*[.!?\n]', text):
        texts.append(subtext.strip())

    return texts


def alphabet_text(text):
    text = re.sub(r"(a|A)", "에이", text)
    text = re.sub(r"(b|B)", "비", text)
    text = re.sub(r"(c|C)", "씨", text)
    text = re.sub(r"(d|D)", "디", text)
    text = re.sub(r"(e|E)", "이", text)
    text = re.sub(r"(f|F)", "에프", text)
    text = re.sub(r"(g|G)", "쥐", text)
    text = re.sub(r"(h|H)", "에이치", text)
    text = re.sub(r"(i|I)", "아이", text)
    text = re.sub(r"(j|J)", "제이", text)
    text = re.sub(r"(k|K)", "케이", text)
    text = re.sub(r"(l|L)", "엘", text)
    text = re.sub(r"(m|M)", "엠", text)
    text = re.sub(r"(n|N)", "엔", text)
    text = re.sub(r"(o|O)", "오", text)
    text = re.sub(r"(p|P)", "피", text)
    text = re.sub(r"(q|Q)", "큐", text)
    text = re.sub(r"(r|R)", "알", text)
    text = re.sub(r"(s|S)", "에스", text)
    text = re.sub(r"(t|T)", "티", text)
    text = re.sub(r"(u|U)", "유", text)
    text = re.sub(r"(v|V)", "브이", text)
    text = re.sub(r"(w|W)", "더블유", text)
    text = re.sub(r"(x|X)", "엑스", text)
    text = re.sub(r"(y|Y)", "와이", text)
    text = re.sub(r"(z|Z)", "지", text)

    return text


def punctuation_text(text):
    # 문장부호
    text = re.sub(r"!", "느낌표", text)
    text = re.sub(r"\?", "물음표", text)
    text = re.sub(r"\.", "마침표", text)

    return text


def jamo_text(text):
    # 기본 자모음
    text = re.sub(r"ㄱ", "기역", text)
    text = re.sub(r"ㄴ", "니은", text)
    text = re.sub(r"ㄷ", "디귿", text)
    text = re.sub(r"ㄹ", "리을", text)
    text = re.sub(r"ㅁ", "미음", text)
    text = re.sub(r"ㅂ", "비읍", text)
    text = re.sub(r"ㅅ", "시옷", text)
    text = re.sub(r"ㅇ", "이응", text)
    text = re.sub(r"ㅈ", "지읒", text)
    text = re.sub(r"ㅊ", "치읓", text)
    text = re.sub(r"ㅋ", "키읔", text)
    text = re.sub(r"ㅌ", "티읕", text)
    text = re.sub(r"ㅍ", "피읖", text)
    text = re.sub(r"ㅎ", "히읗", text)
    text = re.sub(r"ㄲ", "쌍기역", text)
    text = re.sub(r"ㄸ", "쌍디귿", text)
    text = re.sub(r"ㅃ", "쌍비읍", text)
    text = re.sub(r"ㅆ", "쌍시옷", text)
    text = re.sub(r"ㅉ", "쌍지읒", text)
    text = re.sub(r"ㄳ", "기역시옷", text)
    text = re.sub(r"ㄵ", "니은지읒", text)
    text = re.sub(r"ㄶ", "니은히읗", text)
    text = re.sub(r"ㄺ", "리을기역", text)
    text = re.sub(r"ㄻ", "리을미음", text)
    text = re.sub(r"ㄼ", "리을비읍", text)
    text = re.sub(r"ㄽ", "리을시옷", text)
    text = re.sub(r"ㄾ", "리을티읕", text)
    text = re.sub(r"ㄿ", "리을피읍", text)
    text = re.sub(r"ㅀ", "리을히읗", text)
    text = re.sub(r"ㅄ", "비읍시옷", text)
    text = re.sub(r"ㅏ", "아", text)
    text = re.sub(r"ㅑ", "야", text)
    text = re.sub(r"ㅓ", "어", text)
    text = re.sub(r"ㅕ", "여", text)
    text = re.sub(r"ㅗ", "오", text)
    text = re.sub(r"ㅛ", "요", text)
    text = re.sub(r"ㅜ", "우", text)
    text = re.sub(r"ㅠ", "유", text)
    text = re.sub(r"ㅡ", "으", text)
    text = re.sub(r"ㅣ", "이", text)
    text = re.sub(r"ㅐ", "애", text)
    text = re.sub(r"ㅒ", "얘", text)
    text = re.sub(r"ㅔ", "에", text)
    text = re.sub(r"ㅖ", "예", text)
    text = re.sub(r"ㅘ", "와", text)
    text = re.sub(r"ㅙ", "왜", text)
    text = re.sub(r"ㅚ", "외", text)
    text = re.sub(r"ㅝ", "워", text)
    text = re.sub(r"ㅞ", "웨", text)
    text = re.sub(r"ㅟ", "위", text)
    text = re.sub(r"ㅢ", "의", text)

    return text


def normalize_multiline_text(long_text):
    texts = split_text(long_text)
    normalized_texts = [normalize_text(text).strip() for text in texts]
    return [text for text in normalized_texts if len(text) > 0]

def synthesize(text):
    wavs = synthesizer.tts(text, None, None)
    return wavs

/content/TTS


## 3. 학습한 모델 불러오기

학습한 Glow-TTS와 HiFi-GAN 모델을 불러옵니다.

만약 다른 체크포인트에서 불러오시려면 아래 코드에서 경로를 아래와 같이 적절하게 수정합니다.

```python
synthesizer = Synthesizer(
    "/content/drive/My Drive/Colab Notebooks/data/glowtts-v2/glowtts-v2-May-31-2021_08+17AM-d897f2e/best_model.pth.tar",
    "/content/drive/My Drive/Colab Notebooks/data/glowtts-v2/glowtts-v2-May-31-2021_08+17AM-d897f2e/config.json",
    None,
    "/content/drive/My Drive/Colab Notebooks/data/hifigan-v2/hifigan-v2-May-31-2021_08+26AM-d897f2e/checkpoint_300000.pth.tar",
    "/content/drive/My Drive/Colab Notebooks/data/hifigan-v2/hifigan-v2-May-31-2021_08+26AM-d897f2e/config.json",
    None,
    None,
    False,
)
```

In [7]:
synthesizer = Synthesizer(
    "/content/drive/MyDrive/Colab Notebooks/data/glowtts-v2/glowtts-v2-December-04-2023_10+51AM-3aa165a/checkpoint_70000.pth.tar",
    "/content/drive/MyDrive/Colab Notebooks/data/glowtts-v2/glowtts-v2-December-04-2023_10+51AM-3aa165a/config.json",
    None,
    "/content/drive/MyDrive/Colab Notebooks/data/hifigan-v2/hifigan-v2-December-04-2023_01+59PM-3aa165a/checkpoint_400000.pth.tar",
    "/content/drive/MyDrive/Colab Notebooks/data/hifigan-v2/hifigan-v2-December-04-2023_01+59PM-3aa165a/config.json",
    None,
    None,
    False,
)
symbols = synthesizer.tts_config.characters.characters

/content/TTS/TTS/utils/audio.py:146: FutureWarning: Pass sr=22050, n_fft=1024 as keyword args. From version 0.10 passing these as positional arguments will result in an error
  return librosa.filters.mel(


 > Using model: glow_tts


/content/TTS/TTS/tts/layers/glow_tts/glow.py:84: UserWarning: torch.qr is deprecated in favor of torch.linalg.qr and will be removed in a future PyTorch release.
The boolean parameter 'some' has been replaced with a string parameter 'mode'.
Q, R = torch.qr(A, some)
should be replaced with
Q, R = torch.linalg.qr(A, 'reduced' if some else 'complete') (Triggered internally at ../aten/src/ATen/native/BatchLinearAlgebra.cpp:2426.)
  w_init = torch.qr(torch.FloatTensor(self.num_splits, self.num_splits).normal_())[0]
/usr/local/lib/python3.10/dist-packages/torch/nn/utils/weight_norm.py:30: UserWarning: torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.
  warnings.warn("torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.")


 > Generator Model: hifigan_generator
Removing weight norm...


## 4. 음성 합성

실제 음성 합성을 수행합니다.

`long_text`의 값을 변경하여 다른 문장의 합성도 시도해보실 수 있습니다.

In [8]:
texts = """
아래 문장들은 모델 학습을 위해 사용하지 않은 문장들입니다.
그러니까 외계인이 우리 생각을 읽고 우리 생각을 우리가 다시 생각토록 해서 그 생각이 마치 우리가 생각한 것인 것처럼 속였다는 거냐?
어쩌라는건데?
"""
for text in normalize_multiline_text(texts):
    wav = synthesizer.tts(text, None, None)
    IPython.display.display(IPython.display.Audio(wav, rate=22050))

 > Text splitted to sentences.
['아래 문장들은 모델 학습을 위해 사용하지 않은 문장들입니다.']
 > Processing time: 1.9230456352233887
 > Real-time factor: 0.36721591603744386


 > Text splitted to sentences.
['그러니까 외계인이 우리 생각을 읽고 우리 생각을 우리가 다시 생각토록 해서 그 생각이 마치 우리가 생각한 것인 것처럼 속였다는 거냐?']
 > Processing time: 2.0535619258880615
 > Real-time factor: 0.18835707348515704


 > Text splitted to sentences.
['어쩌라는건데?']
 > Processing time: 0.6833281517028809
 > Real-time factor: 0.21713433457817216


In [9]:
texts = """
경기 시작하자 양 팀 수비에서 실수가 나왔다 1회초 KT는 톱타자 배정대가 중견수 뜬공으로 물러났다 김상수가 켈리 상대로 우전 안타를 때렸는데 우익수 홍창기가 바운드를 제대로 맞추지 못하면서 다리 사이로 타구를 놓쳤다 공이 뒤로 빠진 사이 타자주자 김상수는 2루까지 진루했다
"""
for text in normalize_multiline_text(texts):
    wav = synthesizer.tts(text, None, None)
    IPython.display.display(IPython.display.Audio(wav, rate=22050))

 > Text splitted to sentences.
['경기 시작하자 양 팀 수비에서 실수가 나왔다 일회초 케이티는 톱타자 배정대가 중견수 뜬공으로 물러났다 김상수가 켈리 상대로 우전 안타를 때렸는데 우익수 홍창기가 바운드를 제대로 맞추지 못하면서 다리 사이로 타구를 놓쳤다 공이 뒤로 빠진 사이 타자주자 김상수는 이루까지 진루했다.']
 > Processing time: 4.1054840087890625
 > Real-time factor: 0.18561957119557843


In [10]:
texts = """
네 식구들이 너무 많아 먹을것이 부족하다. 이제 이집에서 나가거라!

형님 이 한겨울에 대체 어디로 간단 말입니까?

그건 내가 알 바가 아니야. 어서 썩 나가거라!

그럼 쌀을 조금이라도 주십시오..

아니, 아무것도 주지 않을거야 나가!

아버지 배고파요. 하얀 쌀밥에 고기가 먹고싶어요.
"""
for text in normalize_multiline_text(texts):
    wav = synthesizer.tts(text, None, None)
    IPython.display.display(IPython.display.Audio(wav, rate=22050))

 > Text splitted to sentences.
['네 식구들이 너무 많아 먹을것이 부족하다.']
 > Processing time: 0.7865180969238281
 > Real-time factor: 0.23599395870305914


 > Text splitted to sentences.
['이제 이집에서 나가거라!']
 > Processing time: 0.5851097106933594
 > Real-time factor: 0.1859244454805824


 > Text splitted to sentences.
['형님 이 한겨울에 대체 어디로 간단 말입니까?']
 > Processing time: 0.9024889469146729
 > Real-time factor: 0.19479132027670845


 > Text splitted to sentences.
['그건 내가 알 바가 아니야.']
 > Processing time: 1.4003682136535645
 > Real-time factor: 0.4907520519876208


 > Text splitted to sentences.
['어서 썩 나가거라!']
 > Processing time: 0.9093356132507324
 > Real-time factor: 0.3046871242429287


 > Text splitted to sentences.
['그럼 쌀을 조금이라도 주십시오.']
 > Processing time: 1.167898178100586
 > Real-time factor: 0.3192838081124519


 > Text splitted to sentences.
['아니.', '아무것도 주지 않을거야 나가!']
 > Processing time: 1.5063397884368896
 > Real-time factor: 0.31179401035439896


 > Text splitted to sentences.
['아버지 배고파요.']
 > Processing time: 0.9269700050354004
 > Real-time factor: 0.31550519589760706


 > Text splitted to sentences.
['하얀 쌀밥에 고기가 먹고싶어요.']
 > Processing time: 1.3750958442687988
 > Real-time factor: 0.32267222209823576


In [11]:
texts = """
지드래곤은 이날 마약을 투약했나라는 질문에 재차 하지 않았다고 부인했다. 지드래곤은 지난 6일 인천경찰청 마약수사계에 자진 출석했고 경찰은 국립과학수사연구원에 지드래곤의 모발과 손톱에 대한 정밀 감정을 의뢰했다. 지드래곤은 국과수 정밀 감정 결과에 대해 당연히 음성이 나와야 할 것이라며 마약을 투약한 적도 누군가에게 주고 받은 적 또한 없기 때문에 몸에서 만약 마약 성분이 검출 된다면 그게 더 이상한 것이라고 말했다.
"""
for text in normalize_multiline_text(texts):
    wav = synthesizer.tts(text, None, None)
    IPython.display.display(IPython.display.Audio(wav, rate=22050))

 > Text splitted to sentences.
['지드래곤은 이날 마약을 투약했나라는 질문에 재차 하지 않았다고 부인했다.']
 > Processing time: 1.5451688766479492
 > Real-time factor: 0.2604177397738113


 > Text splitted to sentences.
['지드래곤은 지난 육일 인천경찰청 마약수사계에 자진 출석했고 경찰은 국립과학수사연구원에 지드래곤의 모발과 손톱에 대한 정밀 감정을 의뢰했다.']
 > Processing time: 2.138331413269043
 > Real-time factor: 0.1881192453821513


 > Text splitted to sentences.
['지드래곤은 국과수 정밀 감정 결과에 대해 당연히 음성이 나와야 할 것이라며 마약을 투약한 적도 누군가에게 주고 받은 적 또한 없기 때문에 몸에서 만약 마약 성분이 검출 된다면 그게 더 이상한 것이라고 말했다.']
 > Processing time: 2.7507307529449463
 > Real-time factor: 0.1930856628585674
